## Classifing audio data with convolutional neural networks
by Eduardo Garcia Rajo @ 2019<br/>
<br/>
This notebook if part of the project [Urban sounds classification with Covnolutional Neural Networks](https://github.com/GorillaBus/urban-audio-classifier) on my Github.<br/>
<br/>
Licensed under the GNU LESSER GENERAL PUBLIC LICENSE Version 3, 29 June 2007<br/>
<br/>

### Introduction

In this first notebook we will explore how the data is distributed in means of digital audio properties and dataset categories. We'll also analize the convenience (or inconvinience) of filtering the dataset and working with converted audio files.<br/>
<br/>
Please make sure you have download the UrbanSound8K dataset from: https://urbansounddataset.weebly.com/urbansound8k.html.<br/>
<br/>
Also Visit the [project home](https://github.com/GorillaBus/urban-audio-classifier) on Github for references, requirements, notes and to follow the project addequately.<br/>
<br/>
This work assumes the reader has a good understanding of the basics of digital audio and signal processing, but in case you need some preparation dont worry, just check the references section in the project Github page to follow some very simple tutorials and articles I have shared for this purpose.<br/>
<br/>
Let's get started!<br/>
<br/>

### The dataset: UrbanSound8K

<br/>
The UrbanSound8K dataset contains 8732 labeled sound slices of varying duration up to 4 seconds. The categorization labels being:

* Air Conditioner
* Car Horn
* Children Playing
* Dog bark
* Drilling
* Engine Idling
* Gun Shot
* Jackhammer
* Siren
* Street Music

Note that the dataset comes already organized in 10 validation folds. In the case we want to compare our results with other we should stick with this schema.

<br/>

#### Dataset metadata

The included metadata file ("UrbanSound8K/metadata/metadata.csv") provides all the required information about each audio file:

* slice_file_name: The name of the audio file.
* fsID: The Freesound ID of the recording from which this excerpt (slice) is taken
* start: The start time of the slice in the original Freesound recording
* end: The end time of slice in the original Freesound recording
* salience: A (subjective) salience rating of the sound. 1 = foreground, 2 = background.
* fold: The fold number (1-10) to which this file has been allocated.
* classID: A numeric identifier of the sound class.
* class: The class label name.

For now only "slice_file_name", "fold" and "class" are of our interest.

<br/>

#### Digital audio properties

The main features that describe digital audio are:

* Channels: number of audio chanels (mono/stereo).
* Sample Rate: samples per second expressed in kiloHertz (kHz), related audio quality.
* Bit Depth: equal to resolution in images, describes level of detail. 
* Duration: length of the sound over time.

Data is organization inside an audio file will differ with different properties, in means of scale, or shape for example. Our first task is to determine how are this different audio properties distributed among the dataset and evaluate how we may normalize them, for example, by conversion.<br/>
<br/>

#### Setup
Pay attention to the very simple path variables configured in this section.

In [1]:
# Required libraries
import os
import pandas as pd
import IPython as IP
import struct
import matplotlib.pyplot as plt
import numpy as np

# Set your path to the original dataset
us8k_path = os.path.abspath('./UrbanSound8K' )

# Global settings
metadata_path = os.path.join(us8k_path, 'metadata/UrbanSound8K.csv')
audio_path = os.path.join(us8k_path, 'audio')


#### Helper functions

In [7]:
# Reads a file's header data and returns a list of wavefile properties
def read_header(filename):
    wave = open(filename,"rb")
    riff = wave.read(12)
    fmat = wave.read(36)
    num_channels_string = fmat[10:12]
    num_channels = struct.unpack('<H', num_channels_string)[0]
    sample_rate_string = fmat[12:16]
    sample_rate = struct.unpack("<I",sample_rate_string)[0]
    bit_depth_string = fmat[22:24]
    bit_depth = struct.unpack("<H",bit_depth_string)[0]
    return (num_channels, sample_rate, bit_depth)

# Given a dataset row it returns an audio player and prints the audio properties
def play_dataset_sample(dataset_row):
    fold_num = dataset_row.iloc[0]['fold']
    file_name = dataset_row.iloc[0]['file']
    file_path = os.path.join(audio_path, fold_num, file_name)
    print("Class:", 'children_playing')
    print("File:", file_path)
    print("Sample rate:", dataset_row.iloc[0]['sample_rate'])
    print("Bit depth:", dataset_row.iloc[0]['bit_depth'])
    print("Duration {} seconds".format(dataset_row.iloc[0]['duration']))
    
    # Sound preview
    return IP.display.Audio(file_path)

## Exploring the dataset

### Load metadata

In [3]:
print("Loading CSV file {}".format(metadata_path))

# Load metadata as a Pandas dataframe
metadata = pd.read_csv(metadata_path)

# Examine dataframe's head
metadata.head()

Loading CSV file /home/edu/Projects/urban-audio-classifier/UrbanSound8K/metadata/UrbanSound8K.csv


slice_file_name    fsID  start        end  salience  fold  classID  \
0    100032-3-0-0.wav  100032    0.0   0.317551         1     5        3   
1  100263-2-0-117.wav  100263   58.5  62.500000         1     5        2   
2  100263-2-0-121.wav  100263   60.5  64.500000         1     5        2   
3  100263-2-0-126.wav  100263   63.0  67.000000         1     5        2   
4  100263-2-0-137.wav  100263   68.5  72.500000         1     5        2   

              class  
0          dog_bark  
1  children_playing  
2  children_playing  
3  children_playing  
4  children_playing

### Determining class distribution in our data
How are the samples distributed among the ten different categories?

In [4]:
# Class distribution
metadata['class'].value_counts()

jackhammer          1000
air_conditioner     1000
dog_bark            1000
engine_idling       1000
street_music        1000
children_playing    1000
drilling            1000
siren                929
car_horn             429
gun_shot             374
Name: class, dtype: int64

The population is well distributed between the first 8 classes but we observe a significant difference between those and the two other classes "car_horn" and "gun_shot". 
This may or may not be a concern, we'll see how it impacts on predicting that specific classes once we have a model.

<br/>

### Determining audio properties distribution
Sample Rate, Bit Depth, Audio channels, Sample duration. How is our dataset distributed in respect to all this properties?

<br/>

In [5]:
# Read every file header to collect audio properties
audiodata = []
for index, row in metadata.iterrows():
    cat = str(row["class"])
    fold = 'fold'+str(row["fold"])
    name = str(row["slice_file_name"])
    file_name = os.path.join(audio_path, fold, name)
    audio_props = read_header(file_name)
    duration = row['end'] - row['start']
    audiodata.append((name, fold, cat, duration) + audio_props)

# Convert into a Pandas dataframe
audiodatadf = pd.DataFrame(audiodata, columns=['file', 'fold', 'class', 'duration', 'channels','sample_rate','bit_depth'])

#### Display the history for audio

In [159]:
plt.hist(audiodatadf['duration'], rwidth=0.9, color='#86bf91')

plt.xlabel('Duration')
plt.ylabel('Population')
plt.title('Histogram of audio lengths')
plt.grid(False)
plt.show()

# Count samples with duration > 3 sec
gt_3sec = audiodatadf['duration'][audiodatadf['duration'] > 3].count()
lt_3sec = audiodatadf['duration'][audiodatadf['duration'] < 3].count()
lt_15sec = audiodatadf['duration'][audiodatadf['duration'] < 1.5].count()

# Display counts of interest
print("Greater than 3 seconds: {}".format(gt_3sec))
print("Lower than 3 seconds: {}".format(lt_3sec))
print("Lower than 1.5 seconds: {}".format(lt_15sec))

Greater than 3 seconds: 7468
Lower than 3 seconds: 1264
Lower than 1.5 seconds: 785


Most samples have a duration greater than 3 seconds. Only the ~14.4% of the dataset has less than 3 seconds and ~8.5% is lower than 1.5 seconds.<br/>
<br/>
##### Preserving Spatial Size
Our CNN model will require equal size input vectors. The way to achieve this with a dataset of varying durations is by using padding (filling up empty space with zeros). This is a very common technique and it does not affect the capability of the filters to recognize patterns, with no effect on classification performance:

From the Stanford lectures on Conv Nets (cs231n):<br/>
*"In addition to the aforementioned benefit of keeping the spatial sizes constant after CONV, doing this actually improves performance. If the CONV layers were to not zero-pad the inputs and only perform valid convolutions, then the size of the volumes would reduce by a small amount after each CONV, and the information at the borders would be “washed away” too quickly."*

<br/>

#### Audio Channels

In [160]:
print(audiodatadf.channels.value_counts(normalize=True))



Channels
2    0.915369
1    0.084631
Name: channels, dtype: float64


Most files (>91%) are Stereo (two separated channels). This is not a problem, channel mixing is a very common technique in digital audio processing. We are going to mix stereo channels into a mono mix and work with single channel audio.

<br/>

#### Bith depth

In [202]:
print("Bit depths:\n")
print(audiodatadf.bit_depth.value_counts(normalize=True))

Bit depths:

16    0.659414
24    0.315277
32    0.019354
8     0.004924
4     0.001031
Name: bit_depth, dtype: float64


Found samples from 4bit to 32bit. The difference in audio quality between 4bit and 32bit is extreme.

A a rough reference:
* 32bit / 24bit audio: used for professional audio recording.
* 16bit audio: CD playback, most quality streaming playback.
* 8bit / 4bit: old gaming audio quality, nowadays used to 'destroy' audio as an artistic effect.

<br/>

Different bit depths means different scales and shapes in our data. This is another property that requires normalization.

#### Sample Rates

In [204]:
print("Sample rates:\n")
print(audiodatadf.sample_rate.value_counts(normalize=True))

Sample rates:

44100     0.614979
48000     0.286532
96000     0.069858
24000     0.009391
16000     0.005153
22050     0.005039
11025     0.004466
192000    0.001947
8000      0.001374
11024     0.000802
32000     0.000458
Name: sample_rate, dtype: float64


We have samples between 8khz and 192khz. In terms of audio quality there is a huge difference between 8khz and 192khz, although, at some point the difference is hardly noticeable by the human ear. 

A rough reference:
* 96khz - 192khz: common sample rates in professional audio recording.
* 44.1khz - 48khz: common sample rates in audio playback (CD/DVD/Streaming).
* 22.05khz: low quality sample rates, common in low bandwidth streaming.
* 8khz - 11khz: extremely low quality sample rates.

<br/>

## Listening to the data
Taking a closer "look" to our data we'll listen to some random samples per class and examine the digital audio properties of each case. I recommend you to use the best sound speakers/headphones you have at home and pay attention to the sound; the data we are working with.<br/>
<br/>
See if you can appreciate the difference between different sample rates: can you still recognize sound when sample rate is too low? Do you distinguish any difference between the highest sample rates?<br/>
<br/>
If you cannot reproduce some of this files it may mean you need to install missing audio codecs in your system. Make sure to check for audio codec packs for your operating system.<br/><br/>

(Press Ctrl + Enter to re-randomize the sound on each cell)
<br/>
<br/>

#### Children playing

In [10]:
class_name = 'children_playing'
row = audiodatadf[audiodatadf['class'] == class_name].sample(1)
play_dataset_sample(row)


Class: children_playing
File: /home/edu/Projects/urban-audio-classifier/UrbanSound8K/audio/fold10/155262-2-0-2.wav
Sample rate: 44100
Bit depth: 24
Duration 4.0 seconds


#### Engine idling

In [221]:
class_name = 'engine_idling'
row = audiodatadf[audiodatadf['class'] == class_name].sample(1)
play_dataset_sample(row)

Class: children_playing
File: /home/edu/Projects/nn-audio-classifier/UrbanSound8K/audio/fold1/113205-5-0-0.wav
Sample rate: 96000
Bit depth: 24
Duration 3.24 seconds


#### Street music

In [222]:
class_name = 'street_music'
row = audiodatadf[audiodatadf['class'] == class_name].sample(1)
play_dataset_sample(row)

Class: children_playing
File: /home/edu/Projects/nn-audio-classifier/UrbanSound8K/audio/fold7/115242-9-0-83.wav
Sample rate: 44100
Bit depth: 16
Duration 4.0 seconds


#### Jackhammer

In [240]:
class_name = 'jackhammer'
row = audiodatadf[audiodatadf['class'] == class_name].sample(1)
play_dataset_sample(row)

Class: children_playing
File: /home/edu/Projects/nn-audio-classifier/UrbanSound8K/audio/fold4/22883-7-36-2.wav
Sample rate: 48000
Bit depth: 16
Duration 4.0 seconds


#### Air conditioner

In [224]:
class_name = 'air_conditioner'
row = audiodatadf[audiodatadf['class'] == class_name].sample(1)
play_dataset_sample(row)

Class: children_playing
File: /home/edu/Projects/nn-audio-classifier/UrbanSound8K/audio/fold4/146709-0-0-12.wav
Sample rate: 44100
Bit depth: 24
Duration 4.0 seconds


#### Drilling

In [225]:
class_name = 'drilling'
row = audiodatadf[audiodatadf['class'] == class_name].sample(1)
play_dataset_sample(row)

Class: children_playing
File: /home/edu/Projects/nn-audio-classifier/UrbanSound8K/audio/fold1/17913-4-2-0.wav
Sample rate: 44100
Bit depth: 16
Duration 1.9463659999999994 seconds


#### Dog bark

In [226]:
class_name = 'dog_bark'
row = audiodatadf[audiodatadf['class'] == class_name].sample(1)
play_dataset_sample(row)

Class: children_playing
File: /home/edu/Projects/nn-audio-classifier/UrbanSound8K/audio/fold3/44831-3-0-0.wav
Sample rate: 44100
Bit depth: 16
Duration 4.000000000000001 seconds


#### Siren

In [227]:
class_name = 'siren'
row = audiodatadf[audiodatadf['class'] == class_name].sample(1)
play_dataset_sample(row)

Class: children_playing
File: /home/edu/Projects/nn-audio-classifier/UrbanSound8K/audio/fold6/74726-8-0-2.wav
Sample rate: 44100
Bit depth: 16
Duration 4.0 seconds


#### Car horn

In [241]:
class_name = 'car_horn'
row = audiodatadf[audiodatadf['class'] == class_name].sample(1)
play_dataset_sample(row)

Class: children_playing
File: /home/edu/Projects/nn-audio-classifier/UrbanSound8K/audio/fold8/164626-1-0-0.wav
Sample rate: 48000
Bit depth: 16
Duration 0.7747850000000001 seconds


#### Gun shot

In [9]:
class_name = 'gun_shot'
row = audiodatadf[audiodatadf['class'] == class_name].sample(1)
play_dataset_sample(row)

Class: children_playing
File: /home/edu/Projects/urban-audio-classifier/UrbanSound8K/audio/fold1/46656-6-0-0.wav
Sample rate: 44100
Bit depth: 16
Duration 1.418379 seconds


## Conclusions

We found a large variation range on every digital audio property. To work with consistent data we must normalize this by converting all the audio data files to the same format.<br/>
<br/>
#### To filtering or not to filter
A possible problem may be that converting between extremely different sample rates may end in some audio degradation (see "Aliasing" in the references) and in the loss of audible frequencies. Considering the huge variation we encounter -and considering the unavoidable task of conversion- we must consider one of the two options:<br/>
<br/>

Working only with 16/32 bit, 22.05khz/192khz audio: centering our criterion in audio quality.

or

Working with the full dataset: consider any possible audio artifacts as a noise factor that could help the model generalize better.<br/>
<br/>
Despite the extremely bad quality (a noisy and unnatural performance) of 4/8 bit and sample < 44.1000 khz audio, that audio samples will still contain recognizable sound patterns for our model to learn. So, at least for starting, we are not going to filter the dataset.<br/>
<br/>

#### How to normalize the dataset in terms of audio properties
The only answer is conversion. We can convert all the files to the same audio format/codec and work with the converted dataset or we may convert files on load time.<br/>
<br/>
My first attemp was to use 'ffmpeg' for fast conversions -compared to conversors in native Python libraries-. But as we'll see on the next notebook on data pre-processing, some of those "slow" native Python libraries will give us simplified interfaces to robust data conversion and accurate feature extraction that will be worth the processing time difference.<br/>
<br/>
Next notebook: 2-data-pre-processing.<br/>
<br/>